In [41]:
import pandas as pd
import numpy as np
from sklearn import datasets
from sklearn.datasets import make_regression
from sklearn.model_selection import train_test_split
import pickle
import joblib

from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor

from sklearn.metrics import mean_squared_error
from sklearn.metrics import r2_score
from sklearn.preprocessing import RobustScaler, StandardScaler, MinMaxScaler
from sklearn.preprocessing import OneHotEncoder, OrdinalEncoder

from xgboost import XGBRegressor
import xgboost as xgb
from sklearn.linear_model import Ridge
from sklearn.svm import SVR

from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV

import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.feature_selection import VarianceThreshold

import category_encoders
from category_encoders import TargetEncoder

import catboost as cb

Loading CSVs
==

In [42]:
d_city = pd.read_csv('../data/diamonds_city.csv')
d_clarity = pd.read_csv('../data/diamonds_clarity.csv')
d_color = pd.read_csv('../data/diamonds_color.csv')
d_cut = pd.read_csv('../data/diamonds_cut.csv')
d_dimensions = pd.read_csv('../data/diamonds_dimensions.csv')
d_properties = pd.read_csv('../data/diamonds_properties.csv')
d_transactional = pd.read_csv('../data/diamonds_transactional.csv')
d_test = pd.read_csv('../data/diamonds_test.csv')

In [43]:
diamonds = d_dimensions.merge(d_properties, how='inner', on='index_id')
diamonds = diamonds.merge(d_cut, how='inner', on='cut_id')
diamonds = diamonds.merge(d_color, how='inner', on='color_id')
diamonds = diamonds.merge(d_clarity, how='inner', on='clarity_id')
diamonds = diamonds.merge(d_transactional, how='inner', on='index_id')
diamonds = diamonds.merge(d_city, how='inner', on='city_id')
diamonds = diamonds.drop(columns=['cut_id', 'color_id', 'clarity_id', 'city_id'])
diamonds

index_id  depth  table     x  \
0      5feceb66ffc86f38d952786c6d696c79c2dbc239dd4e91...   62.4   58.0  6.83   
1      248aa2bdd0032920ac9e5f6ad36c350549da067efeaf7b...   60.8   60.0  6.85   
2      72b31cf00f8ab3967588fad4a32f61622cb162f9b7bc2c...   60.6   59.0  4.34   
3      98c53df687f2e9b94da80eef5b9049f1fac456b4c41c80...   62.6   57.0  6.80   
4      5dfe43a321c6834c7de273c73aeadc705d919a5869e0f5...   59.4   62.0  6.66   
...                                                  ...    ...    ...   ...   
40450  e03a231c5b52635043e7dc5f0c6c9f16722e14dbcc98bb...   61.8   56.0  4.42   
40451  90dcb905e13140ff99770039b843fb62fb179ab4a3bae9...   61.6   56.0  4.43   
40452  97d3c3344c245422ee7fa4f448b2cace9940121620df22...   62.4   55.0  4.20   
40453  e4dc4e0761ccc6fbb4c064517e40f3582522c325f9a4e5...   62.0   58.0  6.44   
40454  1b0adf72e2b3e43901d3b38cac535eecd62455882522dc...   62.0   57.0  6.65   

          y     z      cut color clarity  price  carat      city  
0      6.79  4.25  Premium     J     VS2   4268   1.21  Kimberly  
1      6.89  4.18  Premium     J     VS2   4839   1.20  Kimberly  
2      4.38  2.64  Premium     J     VS2    368   0.30  Kimberly  
3      6.72  4.23  Premium     J     VS2   5053   1.20  Kimberly  
4      6.58  3.93  Premium     J     VS2   3593   1.05  Kimberly  
...     ...   ...      ...   ...     ...    ...    ...       ...  
40450  4.46  2.74    Ideal     F      IF    978   0.33    Zurich  
40451  4.47  2.74    Ideal     F      IF    929   0.32    Zurich  
40452  4.17  2.61    Ideal     F      IF    828   0.28    Zurich  
40453  6.49  4.01    Ideal     F      IF  11116   1.02    Zurich  
40454  6.57  4.10    Ideal     F      IF  11233   1.10    Zurich  

[40455 rows x 12 columns]

In [44]:
diamonds

index_id  depth  table     x  \
0      5feceb66ffc86f38d952786c6d696c79c2dbc239dd4e91...   62.4   58.0  6.83   
1      248aa2bdd0032920ac9e5f6ad36c350549da067efeaf7b...   60.8   60.0  6.85   
2      72b31cf00f8ab3967588fad4a32f61622cb162f9b7bc2c...   60.6   59.0  4.34   
3      98c53df687f2e9b94da80eef5b9049f1fac456b4c41c80...   62.6   57.0  6.80   
4      5dfe43a321c6834c7de273c73aeadc705d919a5869e0f5...   59.4   62.0  6.66   
...                                                  ...    ...    ...   ...   
40450  e03a231c5b52635043e7dc5f0c6c9f16722e14dbcc98bb...   61.8   56.0  4.42   
40451  90dcb905e13140ff99770039b843fb62fb179ab4a3bae9...   61.6   56.0  4.43   
40452  97d3c3344c245422ee7fa4f448b2cace9940121620df22...   62.4   55.0  4.20   
40453  e4dc4e0761ccc6fbb4c064517e40f3582522c325f9a4e5...   62.0   58.0  6.44   
40454  1b0adf72e2b3e43901d3b38cac535eecd62455882522dc...   62.0   57.0  6.65   

          y     z      cut color clarity  price  carat      city  
0      6.79  4.25  Premium     J     VS2   4268   1.21  Kimberly  
1      6.89  4.18  Premium     J     VS2   4839   1.20  Kimberly  
2      4.38  2.64  Premium     J     VS2    368   0.30  Kimberly  
3      6.72  4.23  Premium     J     VS2   5053   1.20  Kimberly  
4      6.58  3.93  Premium     J     VS2   3593   1.05  Kimberly  
...     ...   ...      ...   ...     ...    ...    ...       ...  
40450  4.46  2.74    Ideal     F      IF    978   0.33    Zurich  
40451  4.47  2.74    Ideal     F      IF    929   0.32    Zurich  
40452  4.17  2.61    Ideal     F      IF    828   0.28    Zurich  
40453  6.49  4.01    Ideal     F      IF  11116   1.02    Zurich  
40454  6.57  4.10    Ideal     F      IF  11233   1.10    Zurich  

[40455 rows x 12 columns]

Features
==

In [45]:
def super_feature(df):
    return  (df['carat'] / df['table'] * df['depth'])

diamonds['super_feature'] = super_feature(diamonds)

diamonds

index_id  depth  table     x  \
0      5feceb66ffc86f38d952786c6d696c79c2dbc239dd4e91...   62.4   58.0  6.83   
1      248aa2bdd0032920ac9e5f6ad36c350549da067efeaf7b...   60.8   60.0  6.85   
2      72b31cf00f8ab3967588fad4a32f61622cb162f9b7bc2c...   60.6   59.0  4.34   
3      98c53df687f2e9b94da80eef5b9049f1fac456b4c41c80...   62.6   57.0  6.80   
4      5dfe43a321c6834c7de273c73aeadc705d919a5869e0f5...   59.4   62.0  6.66   
...                                                  ...    ...    ...   ...   
40450  e03a231c5b52635043e7dc5f0c6c9f16722e14dbcc98bb...   61.8   56.0  4.42   
40451  90dcb905e13140ff99770039b843fb62fb179ab4a3bae9...   61.6   56.0  4.43   
40452  97d3c3344c245422ee7fa4f448b2cace9940121620df22...   62.4   55.0  4.20   
40453  e4dc4e0761ccc6fbb4c064517e40f3582522c325f9a4e5...   62.0   58.0  6.44   
40454  1b0adf72e2b3e43901d3b38cac535eecd62455882522dc...   62.0   57.0  6.65   

          y     z      cut color clarity  price  carat      city  \
0      6.79  4.25  Premium     J     VS2   4268   1.21  Kimberly   
1      6.89  4.18  Premium     J     VS2   4839   1.20  Kimberly   
2      4.38  2.64  Premium     J     VS2    368   0.30  Kimberly   
3      6.72  4.23  Premium     J     VS2   5053   1.20  Kimberly   
4      6.58  3.93  Premium     J     VS2   3593   1.05  Kimberly   
...     ...   ...      ...   ...     ...    ...    ...       ...   
40450  4.46  2.74    Ideal     F      IF    978   0.33    Zurich   
40451  4.47  2.74    Ideal     F      IF    929   0.32    Zurich   
40452  4.17  2.61    Ideal     F      IF    828   0.28    Zurich   
40453  6.49  4.01    Ideal     F      IF  11116   1.02    Zurich   
40454  6.57  4.10    Ideal     F      IF  11233   1.10    Zurich   

       super_feature  
0           1.301793  
1           1.216000  
2           0.308136  
3           1.317895  
4           1.005968  
...              ...  
40450       0.364179  
40451       0.352000  
40452       0.317673  
40453       1.090345  
40454       1.196491  

[40455 rows x 13 columns]

In [46]:
x_columns = ['depth', 'table','cut', 'color', 'clarity', 'carat', 'super_feature']
X = diamonds[x_columns]

y = diamonds['price']

## Label Encoding
---

In [47]:
cut_encoding = {'Premium':4, 'Very Good':3, 'Fair':2, 'Good': 1, 'Ideal':0}
def labelEncodingForCut(x):
    for key in cut_encoding:
        if x == key:
            return cut_encoding[key]

In [48]:
color_encoding = {'J':6, 'I':5, 'H':4, 'G': 3, 'F':2, 'E':1, 'D':0}
def labelEncodingForColor(x):
    for key in color_encoding:
        if x == key:
            return color_encoding[key]

In [49]:
clarity_encoding = {'I1':0, 'SI2':1, 'SI1':2, 'VS2': 3, 'VS1':4, 'VVS2':5, 'VVS1':6, 'IF':7}
def labelEncodingForClarity(x):
    for key in clarity_encoding:
        if x == key:
            return clarity_encoding[key]

---

In [50]:
X['cut'] = X['cut'].apply(labelEncodingForCut)
X

/var/folders/n3/xb6jll3d49q147jw5_13y6zm0000gn/T/ipykernel_16794/2931406157.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  X['cut'] = X['cut'].apply(labelEncodingForCut)


depth  table  cut color clarity  carat  super_feature
0       62.4   58.0    4     J     VS2   1.21       1.301793
1       60.8   60.0    4     J     VS2   1.20       1.216000
2       60.6   59.0    4     J     VS2   0.30       0.308136
3       62.6   57.0    4     J     VS2   1.20       1.317895
4       59.4   62.0    4     J     VS2   1.05       1.005968
...      ...    ...  ...   ...     ...    ...            ...
40450   61.8   56.0    0     F      IF   0.33       0.364179
40451   61.6   56.0    0     F      IF   0.32       0.352000
40452   62.4   55.0    0     F      IF   0.28       0.317673
40453   62.0   58.0    0     F      IF   1.02       1.090345
40454   62.0   57.0    0     F      IF   1.10       1.196491

[40455 rows x 7 columns]

In [51]:
X['color'] = X['color'].apply(labelEncodingForColor)
X

/var/folders/n3/xb6jll3d49q147jw5_13y6zm0000gn/T/ipykernel_16794/1291655416.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  X['color'] = X['color'].apply(labelEncodingForColor)


depth  table  cut  color clarity  carat  super_feature
0       62.4   58.0    4      6     VS2   1.21       1.301793
1       60.8   60.0    4      6     VS2   1.20       1.216000
2       60.6   59.0    4      6     VS2   0.30       0.308136
3       62.6   57.0    4      6     VS2   1.20       1.317895
4       59.4   62.0    4      6     VS2   1.05       1.005968
...      ...    ...  ...    ...     ...    ...            ...
40450   61.8   56.0    0      2      IF   0.33       0.364179
40451   61.6   56.0    0      2      IF   0.32       0.352000
40452   62.4   55.0    0      2      IF   0.28       0.317673
40453   62.0   58.0    0      2      IF   1.02       1.090345
40454   62.0   57.0    0      2      IF   1.10       1.196491

[40455 rows x 7 columns]

In [52]:
X['clarity'] = X['clarity'].apply(labelEncodingForClarity)
X

/var/folders/n3/xb6jll3d49q147jw5_13y6zm0000gn/T/ipykernel_16794/1828486422.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  X['clarity'] = X['clarity'].apply(labelEncodingForClarity)


depth  table  cut  color  clarity  carat  super_feature
0       62.4   58.0    4      6        3   1.21       1.301793
1       60.8   60.0    4      6        3   1.20       1.216000
2       60.6   59.0    4      6        3   0.30       0.308136
3       62.6   57.0    4      6        3   1.20       1.317895
4       59.4   62.0    4      6        3   1.05       1.005968
...      ...    ...  ...    ...      ...    ...            ...
40450   61.8   56.0    0      2        7   0.33       0.364179
40451   61.6   56.0    0      2        7   0.32       0.352000
40452   62.4   55.0    0      2        7   0.28       0.317673
40453   62.0   58.0    0      2        7   1.02       1.090345
40454   62.0   57.0    0      2        7   1.10       1.196491

[40455 rows x 7 columns]

---

Scaling
==

In [53]:
def scaling(df):
    
    scaler = RobustScaler()
    scaling = scaler.fit_transform(df)
    scaled_df = pd.DataFrame(scaling)
    
    return scaled_df

In [54]:
x_scaling = scaling(X)
x_scaling

0         1    2         3    4         5         6
0      0.400000  0.333333  0.5  1.000000  0.0  0.796875  0.770402
1     -0.666667  1.000000  0.5  1.000000  0.0  0.781250  0.650007
2     -0.800000  0.666667  0.5  1.000000  0.0 -0.625000 -0.624016
3      0.533333  0.000000  0.5  1.000000  0.0  0.781250  0.792998
4     -1.600000  1.666667  0.5  1.000000  0.0  0.546875  0.355265
...         ...       ...  ...       ...  ...       ...       ...
40450  0.000000 -0.333333 -0.5 -0.333333  2.0 -0.578125 -0.545369
40451 -0.133333 -0.333333 -0.5 -0.333333  2.0 -0.593750 -0.562460
40452  0.400000 -0.666667 -0.5 -0.333333  2.0 -0.656250 -0.610632
40453  0.133333  0.333333 -0.5 -0.333333  2.0  0.500000  0.473673
40454  0.133333  0.000000 -0.5 -0.333333  2.0  0.625000  0.622630

[40455 rows x 7 columns]

---

Train, Test, Split
==

In [55]:
X_train, X_test, y_train, y_test = train_test_split(x_scaling, y, test_size=0.2, random_state=42)
print(f"X_train: {X_train.shape}, X_test: {X_test.shape}, y_train: {y_train.shape}, y_test: {y_test.shape}")

X_train: (32364, 7), X_test: (8091, 7), y_train: (32364,), y_test: (8091,)


---

## CatBoost
---

In [56]:
train_dataset = cb.Pool(X_train, y_train) 
test_dataset = cb.Pool(X_test, y_test)

In [57]:
model = cb.CatBoostRegressor(loss_function='RMSE')

In [58]:
grid = {'iterations': [100, 150, 500],
        'learning_rate': [0.03, 0.1, 0.3],
        'depth': [2, 4, 6, 8],
        'l2_leaf_reg': [0.2, 0.5, 1, 3]}
model.grid_search(grid, train_dataset)

0:	learn: 5491.0911590	test: 5385.4307143	best: 5385.4307143 (0)	total: 64.9ms	remaining: 6.43s
1:	learn: 5349.1229423	test: 5245.5248866	best: 5245.5248866 (1)	total: 71.1ms	remaining: 3.48s
2:	learn: 5209.2103323	test: 5107.5392067	best: 5107.5392067 (2)	total: 77.5ms	remaining: 2.51s
3:	learn: 5071.9509949	test: 4972.1883101	best: 4972.1883101 (3)	total: 80.1ms	remaining: 1.92s
4:	learn: 4940.8309125	test: 4842.5679885	best: 4842.5679885 (4)	total: 82.6ms	remaining: 1.57s
5:	learn: 4817.2674530	test: 4720.5248228	best: 4720.5248228 (5)	total: 85.8ms	remaining: 1.34s
6:	learn: 4697.5583233	test: 4602.1844191	best: 4602.1844191 (6)	total: 87.9ms	remaining: 1.17s
7:	learn: 4580.3420069	test: 4486.4487559	best: 4486.4487559 (7)	total: 90.9ms	remaining: 1.04s
8:	learn: 4463.7699471	test: 4371.0941162	best: 4371.0941162 (8)	total: 94.8ms	remaining: 959ms
9:	learn: 4353.3953383	test: 4262.0132018	best: 4262.0132018 (9)	total: 97.4ms	remaining: 876ms
10:	learn: 4247.1467104	test: 4157.42052

47:	learn: 1091.9834070	test: 1055.7662316	best: 1055.7662316 (47)	total: 128ms	remaining: 139ms
48:	learn: 1084.6483600	test: 1048.7524757	best: 1048.7524757 (48)	total: 133ms	remaining: 138ms
49:	learn: 1074.1973624	test: 1037.9719713	best: 1037.9719713 (49)	total: 137ms	remaining: 137ms
50:	learn: 1065.5172064	test: 1030.0264387	best: 1030.0264387 (50)	total: 140ms	remaining: 135ms
51:	learn: 1059.9909566	test: 1023.5077868	best: 1023.5077868 (51)	total: 143ms	remaining: 132ms
52:	learn: 1053.9112696	test: 1017.0757341	best: 1017.0757341 (52)	total: 146ms	remaining: 130ms
53:	learn: 1047.2210351	test: 1010.6107742	best: 1010.6107742 (53)	total: 150ms	remaining: 128ms
54:	learn: 1041.3310987	test: 1005.0016155	best: 1005.0016155 (54)	total: 158ms	remaining: 129ms
55:	learn: 1029.7902855	test: 993.3489684	best: 993.3489684 (55)	total: 163ms	remaining: 128ms
56:	learn: 1024.7267244	test: 988.6312679	best: 988.6312679 (56)	total: 173ms	remaining: 130ms
57:	learn: 1019.4861828	test: 983.

72:	learn: 748.3616363	test: 728.1106103	best: 728.1106103 (72)	total: 208ms	remaining: 76.8ms
73:	learn: 744.9026557	test: 724.3085460	best: 724.3085460 (73)	total: 211ms	remaining: 74.1ms
74:	learn: 743.5290289	test: 723.8688240	best: 723.8688240 (74)	total: 214ms	remaining: 71.4ms
75:	learn: 741.6453399	test: 722.1565844	best: 722.1565844 (75)	total: 215ms	remaining: 68ms
76:	learn: 740.1674086	test: 720.8685775	best: 720.8685775 (76)	total: 218ms	remaining: 65.1ms
77:	learn: 739.7312544	test: 720.7173498	best: 720.7173498 (77)	total: 220ms	remaining: 62ms
78:	learn: 739.2115852	test: 720.3672360	best: 720.3672360 (78)	total: 225ms	remaining: 59.7ms
79:	learn: 736.5571435	test: 718.4168365	best: 718.4168365 (79)	total: 227ms	remaining: 56.7ms
80:	learn: 733.4543712	test: 715.1539654	best: 715.1539654 (80)	total: 229ms	remaining: 53.7ms
81:	learn: 731.8898770	test: 711.9597752	best: 711.9597752 (81)	total: 230ms	remaining: 50.5ms
82:	learn: 730.0090849	test: 709.7955815	best: 709.795

92:	learn: 1384.7437742	test: 1342.5999350	best: 1342.5999350 (92)	total: 405ms	remaining: 30.5ms
93:	learn: 1378.3802965	test: 1336.2572690	best: 1336.2572690 (93)	total: 414ms	remaining: 26.4ms
94:	learn: 1371.3773091	test: 1329.5618329	best: 1329.5618329 (94)	total: 416ms	remaining: 21.9ms
95:	learn: 1364.9357441	test: 1323.4542157	best: 1323.4542157 (95)	total: 417ms	remaining: 17.4ms
96:	learn: 1357.0618164	test: 1315.3060596	best: 1315.3060596 (96)	total: 418ms	remaining: 12.9ms
97:	learn: 1349.6986687	test: 1308.4201043	best: 1308.4201043 (97)	total: 421ms	remaining: 8.59ms
98:	learn: 1343.8673570	test: 1302.6047294	best: 1302.6047294 (98)	total: 424ms	remaining: 4.28ms
99:	learn: 1338.2416819	test: 1297.1870939	best: 1297.1870939 (99)	total: 428ms	remaining: 0us

bestTest = 1297.187094
bestIteration = 99

3:	loss: 1297.1870939	best: 693.7369814 (2)	total: 1.39s	remaining: 48.7s
0:	learn: 5143.8580770	test: 5041.3853780	best: 5041.3853780 (0)	total: 4.8ms	remaining: 475ms
1:	lea

76:	learn: 915.0317758	test: 882.7359616	best: 882.7359616 (76)	total: 391ms	remaining: 117ms
77:	learn: 911.4840901	test: 879.8660737	best: 879.8660737 (77)	total: 399ms	remaining: 112ms
78:	learn: 908.3232486	test: 876.5190316	best: 876.5190316 (78)	total: 404ms	remaining: 107ms
79:	learn: 905.3186971	test: 873.8266977	best: 873.8266977 (79)	total: 409ms	remaining: 102ms
80:	learn: 899.6046692	test: 868.1579104	best: 868.1579104 (80)	total: 415ms	remaining: 97.4ms
81:	learn: 897.0464465	test: 865.7399572	best: 865.7399572 (81)	total: 420ms	remaining: 92.3ms
82:	learn: 893.5555725	test: 862.4545817	best: 862.4545817 (82)	total: 427ms	remaining: 87.4ms
83:	learn: 890.9274211	test: 859.5375899	best: 859.5375899 (83)	total: 432ms	remaining: 82.3ms
84:	learn: 887.0900572	test: 856.0141874	best: 856.0141874 (84)	total: 437ms	remaining: 77.2ms
85:	learn: 883.2999799	test: 851.9219321	best: 851.9219321 (85)	total: 442ms	remaining: 72ms
86:	learn: 880.5911307	test: 849.6399231	best: 849.63992

...

163:	learn: 564.6953325	test: 585.7054787	best: 585.7054787 (163)	total: 1.14s	remaining: 2.33s
164:	learn: 563.8083202	test: 585.1061816	best: 585.1061816 (164)	total: 1.15s	remaining: 2.33s
165:	learn: 562.9738786	test: 584.5388099	best: 584.5388099 (165)	total: 1.16s	remaining: 2.33s
166:	learn: 562.0413737	test: 583.6938716	best: 583.6938716 (166)	total: 1.16s	remaining: 2.32s
167:	learn: 561.2393261	test: 583.2591767	best: 583.2591767 (167)	total: 1.17s	remaining: 2.31s
168:	learn: 560.5497518	test: 582.6969935	best: 582.6969935 (168)	total: 1.17s	remaining: 2.3s
169:	learn: 559.8479854	test: 582.1144759	best: 582.1144759 (169)	total: 1.19s	remaining: 2.32s
170:	learn: 559.1371795	test: 581.5917904	best: 581.5917904 (170)	total: 1.2s	remaining: 2.31s
171:	learn: 558.5652170	test: 581.0994079	best: 581.0994079 (171)	total: 1.21s	remaining: 2.31s
172:	learn: 557.8233076	test: 580.4721824	best: 580.4721824 (172)	total: 1.21s	remaining: 2.29s
173:	learn: 557.2576875	test: 579.9603497	

272:	learn: 517.3368831	test: 557.5195796	best: 557.5195796 (272)	total: 1.98s	remaining: 1.64s
273:	learn: 516.9275252	test: 557.3231830	best: 557.3231830 (273)	total: 1.98s	remaining: 1.64s
274:	learn: 516.6120495	test: 557.2302283	best: 557.2302283 (274)	total: 1.99s	remaining: 1.63s
275:	learn: 516.2328543	test: 557.0515686	best: 557.0515686 (275)	total: 2s	remaining: 1.62s
276:	learn: 516.0168266	test: 556.9840122	best: 556.9840122 (276)	total: 2.01s	remaining: 1.61s
277:	learn: 515.7774658	test: 556.8655523	best: 556.8655523 (277)	total: 2.01s	remaining: 1.61s
278:	learn: 515.5591007	test: 556.8032890	best: 556.8032890 (278)	total: 2.02s	remaining: 1.6s
279:	learn: 515.2702568	test: 556.6750456	best: 556.6750456 (279)	total: 2.03s	remaining: 1.59s
280:	learn: 514.9847464	test: 556.5217434	best: 556.5217434 (280)	total: 2.04s	remaining: 1.59s
281:	learn: 514.8168696	test: 556.4307229	best: 556.4307229 (281)	total: 2.04s	remaining: 1.58s
282:	learn: 514.3491427	test: 556.2544874	be

361:	learn: 495.5432123	test: 549.6578666	best: 549.6578666 (361)	total: 2.6s	remaining: 992ms
362:	learn: 495.4157694	test: 549.6327403	best: 549.6327403 (362)	total: 2.61s	remaining: 986ms
363:	learn: 495.3056303	test: 549.6526961	best: 549.6327403 (362)	total: 2.62s	remaining: 978ms
364:	learn: 495.1604475	test: 549.6674342	best: 549.6327403 (362)	total: 2.62s	remaining: 970ms
365:	learn: 494.9115637	test: 549.5614000	best: 549.5614000 (365)	total: 2.63s	remaining: 962ms
366:	learn: 494.5204884	test: 549.5783438	best: 549.5614000 (365)	total: 2.63s	remaining: 955ms
367:	learn: 494.2491113	test: 549.5815257	best: 549.5614000 (365)	total: 2.64s	remaining: 948ms
368:	learn: 493.8370010	test: 549.5549505	best: 549.5549505 (368)	total: 2.65s	remaining: 941ms
369:	learn: 493.6110083	test: 549.4540698	best: 549.4540698 (369)	total: 2.65s	remaining: 933ms
370:	learn: 493.3191403	test: 549.4199043	best: 549.4199043 (370)	total: 2.66s	remaining: 926ms
371:	learn: 493.1209718	test: 549.2313219

451:	learn: 478.0648451	test: 546.5010405	best: 546.4968708 (443)	total: 3.22s	remaining: 342ms
452:	learn: 477.9210952	test: 546.4650708	best: 546.4650708 (452)	total: 3.23s	remaining: 335ms
453:	learn: 477.7337792	test: 546.4463384	best: 546.4463384 (453)	total: 3.24s	remaining: 328ms
454:	learn: 477.6373933	test: 546.5199667	best: 546.4463384 (453)	total: 3.24s	remaining: 321ms
455:	learn: 477.5845360	test: 546.4997806	best: 546.4463384 (453)	total: 3.25s	remaining: 314ms
456:	learn: 477.2978927	test: 546.5329245	best: 546.4463384 (453)	total: 3.26s	remaining: 306ms
457:	learn: 477.1034993	test: 546.5486783	best: 546.4463384 (453)	total: 3.27s	remaining: 299ms
458:	learn: 476.8963645	test: 546.5326676	best: 546.4463384 (453)	total: 3.27s	remaining: 292ms
459:	learn: 476.6884294	test: 546.5514358	best: 546.4463384 (453)	total: 3.28s	remaining: 285ms
460:	learn: 476.6001188	test: 546.4989472	best: 546.4463384 (453)	total: 3.28s	remaining: 278ms
461:	learn: 476.4161203	test: 546.519887

{'params': {'depth': 8,
  'iterations': 500,
  'learning_rate': 0.03,
  'l2_leaf_reg': 0.5},
 'cv_results': defaultdict(list,
             {'iterations': [0,
               1,
               2,
               3,
               4,
               5,
               6,
               7,
               8,
               9,
               10,
               11,
               12,
               13,
               14,
               15,
               16,
               17,
               18,
               19,
               20,
               21,
               22,
               23,
               24,
               25,
               26,
               27,
               28,
               29,
               30,
               31,
               32,
               33,
               34,
               35,
               36,
               37,
               38,
               39,
               40,
               41,
               42,
               43,
               44,
               

In [59]:
pred = model.predict(X_test)
rmse = (np.sqrt(mean_squared_error(y_test, pred)))
r2 = r2_score(y_test, pred)
print('Testing performance')
print('RMSE: {:.2f}'.format(rmse))
print('R2: {:.2f}'.format(r2))

Testing performance
RMSE: 514.18
R2: 0.98


Predictions
==

In [60]:

d_test['super_feature'] = super_feature(d_test)

d_test = d_test[x_columns]
d_test['cut'] = d_test['cut'].apply(labelEncodingForCut)
d_test['color'] = d_test['color'].apply(labelEncodingForColor)
d_test['clarity'] = d_test['clarity'].apply(labelEncodingForClarity)
x_pred = scaling(d_test)

d_test

depth  table  cut  color  clarity  carat  super_feature
0       62.7   60.0    3      2        2   0.79       0.825550
1       61.0   57.0    0      6        4   1.20       1.284211
2       62.2   61.0    4      4        2   1.57       1.600885
3       63.8   54.0    3      2        2   0.90       1.063333
4       62.9   58.0    3      2        4   0.50       0.542241
...      ...    ...  ...    ...      ...    ...            ...
13480   61.9   56.0    0      1        2   0.57       0.630054
13481   62.2   55.0    0      5        3   0.71       0.802945
13482   61.6   55.0    0      2        4   0.70       0.784000
13483   58.8   57.0    3      2        1   0.70       0.722105
13484   62.4   55.0    0      5        5   0.40       0.453818

[13485 rows x 7 columns]

In [64]:
d_predictions = model.predict(x_pred).clip(0, 30000)
d_predictions

array([2855.01723764, 5542.24531349, 9685.60183381, ..., 3162.91337669,
       2084.13677741,  843.02440773])

## Save predictions
---

In [65]:
predictions = pd.DataFrame(d_predictions).rename(columns={0:'price'})
predictions.index.names = ['id']
predictions

price
id                
0      2855.017238
1      5542.245313
2      9685.601834
3      3910.636577
4      1577.172380
...            ...
13480  1680.074564
13481  2314.802610
13482  3162.913377
13483  2084.136777
13484   843.024408

[13485 rows x 1 columns]

In [67]:
predictions.to_csv('../results/predictions_catboost1.csv')

---